# Test avec CatBoostRegressor

In [14]:
import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from catboost import CatBoostRegressor

In [15]:
df = pd.read_csv("../data/gold.csv")

In [16]:
# column_titles = df.columns.tolist()
# column_titles

In [23]:
X = df.drop(["prix_median"], axis=1)
y = df['prix_median']
X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.8, shuffle=True, random_state=42)

categorial_features = ["proximité_autoroute"]

numerical_features = ['tx_crim', 'tx_residence','tx_commerce',
       'tx_nitriq', 'nb_piece', 'tx_ancienneté_parc_immo', 'distance_centre_emploi',
        'indice_impot_foncier',  'ratio_eleve_enseignant', 'tx_status_sociaux_eco_inf']

categorical_transformer = OneHotEncoder(sparse_output=True)
numerical_transformer = StandardScaler()

preprocessor = ColumnTransformer(
    transformers=[
        ('cat', categorical_transformer, categorial_features),
        ('num', numerical_transformer, numerical_features)
    ],
    remainder="passthrough" 
)

# Créer un objet CatBoostRegressor
# cb_reg = CatBoostRegressor(random_state=42, verbose=False)
# cb_reg = CatBoostRegressor(depth=4, learning_rate=0.19293408926881367, l2_leaf_reg=1.9445149121337306, random_state=42, verbose=False)
# cb_reg = CatBoostRegressor(iterations = 700, learning_rate = 0.0693060439562983, depth = 6, loss_function = 'RMSE', subsample = 0.30000000000000004, l2_leaf_reg = 0.9500743944149637, random_strength = 0.10292853111379426, random_state=42, verbose=False)
cb_reg = CatBoostRegressor(iterations = 900, learning_rate = 0.0677148890414124, depth = 9, loss_function = 'RMSE', subsample = 0.5, l2_leaf_reg = 9.760330771250379, random_strength = 4.695597681100087, random_state=42, verbose=False)


# Créer un pipeline avec le préprocesseur et le modèle CatBoostRegressor
pipe = Pipeline([
     ('preprocessor', preprocessor),
     ('cb_reg', cb_reg)
])

# Entraîner le pipeline sur les données d'entraînement
pipe.fit(X_train, y_train)
y_pred_train = pipe.predict(X_train)
y_pred_test = pipe.predict(X_test)

print("Mean squared error : ")
print("TRAIN :",mean_squared_error(y_train, y_pred_train))
print("TEST :",mean_squared_error(y_test, y_pred_test))

# print("/////////////////////////////////////////////////////")

print("Mean absolute error : ")
print("TRAIN :",mean_absolute_error(y_train, y_pred_train))
print("TEST :",mean_absolute_error(y_test, y_pred_test))

# print("/////////////////////////////////////////////////////")

print("R2 score : ",r2_score(y_test, y_pred_test))    
print("TRAIN :",r2_score(y_train, y_pred_train))
print("TEST :",r2_score(y_test, y_pred_test))

Mean squared error : 
TRAIN : 0.1559923129043852
TEST : 8.50384599912411
Mean absolute error : 
TRAIN : 0.31679518729962375
TEST : 1.9309213145027615
R2 score :  0.8840391749525192
TRAIN : 0.9982043720399821
TEST : 0.8840391749525192


### Optuna (recherche des hyperparametres)

In [18]:
import optuna
from sklearn.metrics import r2_score

In [19]:
def objective(trial):
    # Définition des hyperparamètres à optimiser
    iterations = trial.suggest_int('iterations', 100, 1000, step=100)
    learning_rate = trial.suggest_float('learning_rate', 0.001, 0.1, log=True)
    depth = trial.suggest_int('depth', 3, 10)
    loss_function = trial.suggest_categorical('loss_function', ['RMSE', 'MAE'])
    subsample = trial.suggest_float('subsample', 0.1, 1.0, step=0.1)
    l2_leaf_reg = trial.suggest_float('l2_leaf_reg', 0.1, 10.0)
    random_strength = trial.suggest_float('random_strength', 0.1, 10.0)
    
    # Création du modèle avec les hyperparamètres suggérés
    model = CatBoostRegressor(iterations=iterations,
                              learning_rate=learning_rate,
                              depth=depth,
                              loss_function=loss_function,
                              subsample=subsample,
                              l2_leaf_reg=l2_leaf_reg,
                              random_strength=random_strength,
                              random_state=42)
    
    # Entraînement du modèle
    model.fit(X_train, y_train)
    
    # Prédiction sur les données de test
    y_pred = model.predict(X_test)
    
    # Calcul du score R2
    r2 = r2_score(y_test, y_pred)
    
    return r2

In [20]:
study = optuna.create_study(direction='maximize')
study.optimize(objective, n_trials=100)

[I 2023-06-14 08:52:04,482] A new study created in memory with name: no-name-8ec95761-39c2-4956-8d04-cb869fce1993


0:	learn: 6.5613092	total: 6.8ms	remaining: 673ms
1:	learn: 6.4489641	total: 12.2ms	remaining: 599ms
2:	learn: 6.3455938	total: 18.5ms	remaining: 598ms
3:	learn: 6.2336149	total: 24.5ms	remaining: 587ms
4:	learn: 6.1468647	total: 26.1ms	remaining: 496ms
5:	learn: 6.0462112	total: 31.5ms	remaining: 493ms
6:	learn: 5.9418074	total: 36.5ms	remaining: 484ms
7:	learn: 5.8440091	total: 41.1ms	remaining: 472ms
8:	learn: 5.7471557	total: 45.9ms	remaining: 464ms
9:	learn: 5.6671024	total: 50.6ms	remaining: 456ms
10:	learn: 5.5715511	total: 56ms	remaining: 453ms
11:	learn: 5.4824214	total: 60.8ms	remaining: 446ms
12:	learn: 5.3972497	total: 65.4ms	remaining: 438ms
13:	learn: 5.3238424	total: 70.8ms	remaining: 435ms
14:	learn: 5.2380816	total: 75.5ms	remaining: 428ms
15:	learn: 5.1543156	total: 80.2ms	remaining: 421ms
16:	learn: 5.0742896	total: 85.9ms	remaining: 419ms
17:	learn: 4.9902324	total: 90.7ms	remaining: 413ms
18:	learn: 4.9211201	total: 95.7ms	remaining: 408ms
19:	learn: 4.8451177	tota

[I 2023-06-14 08:52:05,120] Trial 0 finished with value: 0.7594591020554605 and parameters: {'iterations': 100, 'learning_rate': 0.022071515189511972, 'depth': 9, 'loss_function': 'MAE', 'subsample': 1.0, 'l2_leaf_reg': 4.8964936700904795, 'random_strength': 1.2762636354480725}. Best is trial 0 with value: 0.7594591020554605.


0:	learn: 9.0554716	total: 3.81ms	remaining: 1.14s
1:	learn: 8.7983026	total: 6.98ms	remaining: 1.04s
2:	learn: 8.5044298	total: 9.4ms	remaining: 931ms
3:	learn: 8.2571135	total: 11.7ms	remaining: 868ms
4:	learn: 8.0549385	total: 14.5ms	remaining: 855ms
5:	learn: 7.8010054	total: 17.2ms	remaining: 845ms
6:	learn: 7.6111046	total: 21.3ms	remaining: 893ms
7:	learn: 7.3624173	total: 23.6ms	remaining: 862ms
8:	learn: 7.1475942	total: 26ms	remaining: 842ms
9:	learn: 6.9541522	total: 28.2ms	remaining: 818ms
10:	learn: 6.8463989	total: 30.2ms	remaining: 794ms
11:	learn: 6.7009588	total: 32.5ms	remaining: 780ms
12:	learn: 6.5349400	total: 35.4ms	remaining: 781ms
13:	learn: 6.4253356	total: 37.7ms	remaining: 770ms
14:	learn: 6.2961082	total: 40ms	remaining: 760ms
15:	learn: 6.1549197	total: 42ms	remaining: 745ms
16:	learn: 6.0294049	total: 43.9ms	remaining: 730ms
17:	learn: 5.9198904	total: 45.9ms	remaining: 720ms
18:	learn: 5.7851234	total: 47.9ms	remaining: 709ms
19:	learn: 5.6618206	total: 4

[I 2023-06-14 08:52:05,850] Trial 1 finished with value: 0.889246054762703 and parameters: {'iterations': 300, 'learning_rate': 0.07507995166606489, 'depth': 8, 'loss_function': 'RMSE', 'subsample': 0.30000000000000004, 'l2_leaf_reg': 9.824530990673075, 'random_strength': 3.814168064217667}. Best is trial 1 with value: 0.889246054762703.


...

850:	learn: 0.7501142	total: 2.01s	remaining: 116ms
851:	learn: 0.7478933	total: 2.01s	remaining: 113ms
852:	learn: 0.7468394	total: 2.01s	remaining: 111ms
853:	learn: 0.7453498	total: 2.01s	remaining: 108ms
854:	learn: 0.7445544	total: 2.02s	remaining: 106ms
855:	learn: 0.7436724	total: 2.02s	remaining: 104ms
856:	learn: 0.7429232	total: 2.02s	remaining: 101ms
857:	learn: 0.7411358	total: 2.02s	remaining: 99.1ms
858:	learn: 0.7406663	total: 2.03s	remaining: 96.7ms
859:	learn: 0.7397692	total: 2.03s	remaining: 94.3ms
860:	learn: 0.7383385	total: 2.03s	remaining: 91.9ms
861:	learn: 0.7375573	total: 2.03s	remaining: 89.6ms
862:	learn: 0.7360412	total: 2.04s	remaining: 87.3ms
863:	learn: 0.7343790	total: 2.04s	remaining: 84.9ms
864:	learn: 0.7339662	total: 2.04s	remaining: 82.6ms
865:	learn: 0.7326182	total: 2.04s	remaining: 80.2ms
866:	learn: 0.7311604	total: 2.04s	remaining: 77.8ms
867:	learn: 0.7298458	total: 2.05s	remaining: 75.4ms
868:	learn: 0.7290705	total: 2.05s	remaining: 73.1ms


[I 2023-06-14 08:57:13,977] Trial 98 finished with value: 0.8904649194729867 and parameters: {'iterations': 800, 'learning_rate': 0.07235950766148758, 'depth': 9, 'loss_function': 'RMSE', 'subsample': 0.5, 'l2_leaf_reg': 8.15027077978357, 'random_strength': 4.538600737389177}. Best is trial 69 with value: 0.9053965662800656.


788:	learn: 0.3416106	total: 4.61s	remaining: 64.2ms
789:	learn: 0.3403585	total: 4.61s	remaining: 58.4ms
790:	learn: 0.3402486	total: 4.61s	remaining: 52.5ms
791:	learn: 0.3395535	total: 4.62s	remaining: 46.7ms
792:	learn: 0.3384109	total: 4.62s	remaining: 40.8ms
793:	learn: 0.3379071	total: 4.63s	remaining: 35ms
794:	learn: 0.3367122	total: 4.64s	remaining: 29.2ms
795:	learn: 0.3360895	total: 4.64s	remaining: 23.3ms
796:	learn: 0.3354695	total: 4.65s	remaining: 17.5ms
797:	learn: 0.3353487	total: 4.65s	remaining: 11.7ms
798:	learn: 0.3347015	total: 4.66s	remaining: 5.83ms
799:	learn: 0.3337331	total: 4.66s	remaining: 0us
0:	learn: 8.9919827	total: 8.73ms	remaining: 7.85s
1:	learn: 8.6602568	total: 17.9ms	remaining: 8.06s
2:	learn: 8.3849576	total: 26.7ms	remaining: 7.99s
3:	learn: 8.0699404	total: 35.5ms	remaining: 7.94s
4:	learn: 7.8109678	total: 45.4ms	remaining: 8.13s
5:	learn: 7.5789173	total: 55.5ms	remaining: 8.27s
6:	learn: 7.3511783	total: 66.3ms	remaining: 8.46s
7:	learn: 7.

[I 2023-06-14 08:57:22,941] Trial 99 finished with value: 0.87642991992217 and parameters: {'iterations': 900, 'learning_rate': 0.0906453137691078, 'depth': 10, 'loss_function': 'RMSE', 'subsample': 0.6, 'l2_leaf_reg': 9.54010083238197, 'random_strength': 4.077018815026327}. Best is trial 69 with value: 0.9053965662800656.


885:	learn: 0.1715551	total: 8.54s	remaining: 135ms
886:	learn: 0.1711243	total: 8.55s	remaining: 125ms
887:	learn: 0.1701534	total: 8.56s	remaining: 116ms
888:	learn: 0.1698196	total: 8.57s	remaining: 106ms
889:	learn: 0.1693579	total: 8.58s	remaining: 96.4ms
890:	learn: 0.1690359	total: 8.59s	remaining: 86.8ms
891:	learn: 0.1684321	total: 8.6s	remaining: 77.1ms
892:	learn: 0.1677886	total: 8.61s	remaining: 67.5ms
893:	learn: 0.1677184	total: 8.62s	remaining: 57.8ms
894:	learn: 0.1674981	total: 8.63s	remaining: 48.2ms
895:	learn: 0.1671365	total: 8.64s	remaining: 38.6ms
896:	learn: 0.1668136	total: 8.65s	remaining: 28.9ms
897:	learn: 0.1661501	total: 8.66s	remaining: 19.3ms
898:	learn: 0.1657188	total: 8.67s	remaining: 9.64ms
899:	learn: 0.1652116	total: 8.68s	remaining: 0us


In [21]:
best_params = study.best_params
best_value = study.best_value

In [22]:
print(best_params)
print(best_value)

{'iterations': 900, 'learning_rate': 0.0677148890414124, 'depth': 9, 'loss_function': 'RMSE', 'subsample': 0.5, 'l2_leaf_reg': 9.760330771250379, 'random_strength': 4.695597681100087}
0.9053965662800656
